In [1]:
import gradslam as gs
import matplotlib.pyplot as plt
import numpy as np
import os
import torch
from gradslam import Pointclouds, RGBDImages
from gradslam.datasets import ICL
from gradslam.slam import PointFusion
from torch.utils.data import DataLoader
device = torch.device("cuda:0" if (torch.cuda.is_available()) else "cpu")

In [25]:
icl_path = '/home/cybercore/Workspaces/nam/kansai/output/'
dataset = ICL(icl_path, seqlen=20, width=320, height=240, dilation=0, return_pose=False, return_transform=False)
loader = DataLoader(dataset=dataset, batch_size=2)


In [27]:
colors, depths, intrinsics, poses, *_ = next(iter(loader))
rgbdimages = RGBDImages(colors, depths, intrinsics)
slam = PointFusion(device=device)
pointclouds = Pointclouds(device=device)

In [28]:
batch_size, seq_len = rgbdimages.shape[:2]
initial_poses = torch.eye(4, device=device).view(1, 1, 4, 4).repeat(batch_size, 1, 1, 1)
prev_frame = None

In [29]:
for s in range(seq_len):
    live_frame = rgbdimages[:, s].to(device)
    if s == 0 and live_frame.poses is None:
        live_frame.poses = initial_poses
    pointclouds, live_frame.poses = slam.step(pointclouds, live_frame, prev_frame)
    prev_frame = live_frame

In [30]:
pointclouds.plotly(0, max_num_points=30000).update_layout(autosize=False, width=600).show()